In [1]:
import os
os.chdir(os.path.join(os.getcwd(),'..'))

In [2]:
import numpy as np
import pandas as pd
from scipy.spatial.distance import pdist, squareform

In [3]:
stage_in = lambda x: x[6:7]
age_in = lambda x: x[-2:]

In [4]:
from services import DataReader

X, y = DataReader().read_fva_solutions('fva_without.transports.txt')

In [5]:
_, y = DataReader().read_data('BC_age', True)

y = list(map(stage_in, y))

In [6]:
from preprocessing import DynamicPreprocessing

pre = DynamicPreprocessing(['flux-diff', 'feature-selection','pathway-scoring', 'transport-elimination'])
X_pre = pre.fit_transform(X, y)

In [7]:
_, y = DataReader().read_data('BC_age', True)

In [8]:
from visualization import HeatmapVisualization

heat = HeatmapVisualization(X_pre, y).iplot_heatmap()

In [9]:
df= pd.DataFrame().from_records(X_pre)
pathways = np.array(df.keys())
data_array = df.values
labels = y

In [10]:
import plotly.plotly as py 
from plotly.graph_objs import *  
from plotly import figure_factory as ff
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

from scipy.cluster.hierarchy import linkage

init_notebook_mode(connected=True)

In [11]:
def order_data_by(key):
    ordered_labels, ordered_data = zip(*sorted(zip(labels, data_array), key=key))
    ulabels = list(map(lambda x: '%s_%d' % x, zip(ordered_labels, range(len(ordered_labels)))))
    return np.array(ordered_data), ulabels

In [12]:
ordered_data_array_by_stage_age, ordered_labels_by_stage_age = \
    order_data_by(lambda x: (stage_in(x[0]), age_in(x[0])))
    
heatmap = Heatmap(z=ordered_data_array_by_stage_age.T, x=ordered_labels_by_stage_age, y=pathways)

iplot([heatmap], filename='heatmap_labels_ordered_by_stage_than_age.html')

In [13]:
ordered_data_array_by_age_stage, ordered_labels_by_age_stage = \
    order_data_by(lambda x: (age_in(x[0]), stage_in(x[0])))
    
heatmap = Heatmap(z=ordered_data_array_by_age_stage.T, x=ordered_labels_by_age_stage, y=pathways)

iplot([heatmap], filename='heatmap_labels_ordered_by_stage_than_age.html')

In [14]:
figure = ff.create_dendrogram(data_array, orientation='bottom',
                              linkagefun=lambda x: linkage(data_array, 'complete', metric='correlation'))

dendro_side = ff.create_dendrogram(data_array.T, orientation='right',
                                   linkagefun=lambda x: linkage(data_array.T, 'complete', metric='correlation'))

x_dendro_leaves = list(map(int, figure['layout']['xaxis']['ticktext']))
y_dendro_leaves = list(map(int, dendro_side['layout']['yaxis']['ticktext']))

figure = ff.create_dendrogram(data_array, orientation='bottom', labels=labels,
                              linkagefun=lambda x: linkage(data_array, 'complete', metric='correlation'))

for i in range(len(figure['data'])):
    figure['data'][i]['yaxis'] = 'y2'

dendro_side = ff.create_dendrogram(data_array.T, orientation='right', labels=pathways,
                                   linkagefun=lambda x: linkage(data_array.T, 'complete', metric='correlation'))

for i in range(len(dendro_side['data'])):
    dendro_side['data'][i]['xaxis'] = 'x2'

figure['data'].extend(dendro_side['data'])

heat_data = data_array.T
heat_data = heat_data[y_dendro_leaves,:]
heat_data = heat_data[:,x_dendro_leaves]

heatmap = Data([
    Heatmap(
        x = figure['layout']['xaxis']['tickvals'],
        y = dendro_side['layout']['yaxis']['tickvals'],
        z = heat_data,    
        colorscale = [[0.0, 'rgb(165,0,38)'], [0.1111111111111111, 'rgb(215,48,39)'], [0.2222222222222222, 'rgb(244,109,67)'], [0.3333333333333333, 'rgb(253,174,97)'], [0.4444444444444444, 'rgb(254,224,144)'], [0.5555555555555556, 'rgb(224,243,248)'], [0.6666666666666666, 'rgb(171,217,233)'], [0.7777777777777778, 'rgb(116,173,209)'], [0.8888888888888888, 'rgb(69,117,180)'], [1.0, 'rgb(49,54,149)']]
    )
])

figure['data'].extend(Data(heatmap))
figure['layout'].update({'width':800, 'height':800,'showlegend':False, 'hovermode': 'closest'})

figure['layout']['xaxis'].update({'domain': [.15, 1], 
                                  'mirror': False, 
                                  'showgrid': False, 
                                  'showline': False,
                                  'zeroline': False,
                                  'ticks':""})

figure['layout'].update({'xaxis2': {'domain': [0, .15],
                                   'mirror': False,
                                   'showgrid': False,
                                   'showline': False,
                                   'zeroline': False,
                                   'showticklabels': False,
                                   'ticks':""}})

figure['layout']['yaxis'].update({'domain': [0, .85],
                                  'mirror': False,
                                  'showgrid': False,
                                  'showline': False,
                                  'zeroline': False,
                                  'showticklabels': False,
                                  'ticks': ""})

figure['layout'].update({'yaxis2':{'domain':[.825, .975],
                                   'mirror': False,
                                   'showgrid': False,
                                   'showline': False,
                                   'zeroline': False,
                                   'showticklabels': False,
                                   'ticks':""}})

iplot(figure, filename='heatmap_subject_pathway.html')

In [15]:
figure = ff.create_dendrogram(data_array, orientation='bottom', labels=labels,
                              linkagefun=lambda x: linkage(data_array, 'complete', metric='correlation'))
for i in range(len(figure['data'])):
    figure['data'][i]['yaxis'] = 'y2'

dendro_side = ff.create_dendrogram(data_array, orientation='right',
                                   linkagefun=lambda x: linkage(data_array, 'complete', metric='correlation'))

for i in range(len(dendro_side['data'])):
    dendro_side['data'][i]['xaxis'] = 'x2'

# Add Side Dendrogram Data to Figure
figure['data'].extend(dendro_side['data'])

# Create Heatmap
dendro_leaves = dendro_side['layout']['yaxis']['ticktext']
dendro_leaves = list(map(int, dendro_leaves))
data_dist = pdist(data_array)
heat_data = squareform(data_dist)
heat_data = heat_data[dendro_leaves,:]
heat_data = heat_data[:,dendro_leaves]

heatmap = Data([
    Heatmap(
        x = dendro_leaves, 
        y = dendro_leaves,
        z = heat_data,    
        colorscale = [[0.0, 'rgb(165,0,38)'], [0.1111111111111111, 'rgb(215,48,39)'], [0.2222222222222222, 'rgb(244,109,67)'], [0.3333333333333333, 'rgb(253,174,97)'], [0.4444444444444444, 'rgb(254,224,144)'], [0.5555555555555556, 'rgb(224,243,248)'], [0.6666666666666666, 'rgb(171,217,233)'], [0.7777777777777778, 'rgb(116,173,209)'], [0.8888888888888888, 'rgb(69,117,180)'], [1.0, 'rgb(49,54,149)']]
    )
])

heatmap[0]['x'] = figure['layout']['xaxis']['tickvals']
heatmap[0]['y'] = dendro_side['layout']['yaxis']['tickvals']

# Add Heatmap Data to Figure
figure['data'].extend(Data(heatmap))

# Edit Layout
figure['layout'].update({'width':800, 'height':800,
                         'showlegend':False, 'hovermode': 'closest',
                         })
# Edit xaxis
figure['layout']['xaxis'].update({'domain': [.15, 1],
                                  'mirror': False,
                                  'showgrid': False,
                                  'showline': False,
                                  'zeroline': False,
                                  'ticks':""})
# Edit xaxis2
figure['layout'].update({'xaxis2': {'domain': [0, .15],
                                   'mirror': False,
                                   'showgrid': False,
                                   'showline': False,
                                   'zeroline': False,
                                   'showticklabels': False,
                                   'ticks':""}})

# Edit yaxis
figure['layout']['yaxis'].update({'domain': [0, .85],
                                  'mirror': False,
                                  'showgrid': False,
                                  'showline': False,
                                  'zeroline': False,
                                  'showticklabels': False,
                                  'ticks': ""})
# Edit yaxis2
figure['layout'].update({'yaxis2':{'domain':[.825, .975],
                                   'mirror': False,
                                   'showgrid': False,
                                   'showline': False,
                                   'zeroline': False,
                                   'showticklabels': False,
                                   'ticks':""}})

# Plot!
iplot(figure, filename='heatmap_subject.html')